In [3]:
#---------------------Importing Libraries------------------------------#
import pandas as pd
import numpy as np
import pandas_profiling

In [4]:
#---------------------No limits to rows and columns-------------------#
pd.set_option('max_rows', None)
pd.set_option('max_columns', None)

## Understanding the DATA

In [6]:
data = pd.read_csv("/home/gus/Dropbox/IRONHACK/LABS/Project/project-pandas/GSAF5.csv",encoding='ISO-8859-1')

In [4]:
data.profile_report()

## Dropping Columns with to much null

In [7]:
before = len(data)
data = data.drop_duplicates()
after = len(data)
print('Number of duplicate records dropped: ', str(before - after))



Number of duplicate records dropped:  0


In [11]:
null_cols = data.isnull().sum()
drop_cols = list(null_cols[null_cols > 5000].index)

In [12]:
data = data.drop(drop_cols, axis=1)

In [59]:
data["Area"] = data["Area"].fillna(value="None")
data

Date  Year          Type  \
0                                             18-Sep-16  2016    Unprovoked   
1                                             18-Sep-16  2016    Unprovoked   
2                                             18-Sep-16  2016    Unprovoked   
3                                             17-Sep-16  2016    Unprovoked   
4                                             16-Sep-16  2016    Unprovoked   
5                                             15-Sep-16  2016          Boat   
6                                             11-Sep-16  2016    Unprovoked   
7                                             07-Sep-16  2016    Unprovoked   
8                                             06-Sep-16  2016    Unprovoked   
9                                             05-Sep-16  2016    Unprovoked   
10                                            05-Sep-16  2016    Unprovoked   
11                                            04-Sep-16  2016    Unprovoked   
12                                            01-Sep-16  2016    Unprovoked   
13                                            29-Aug-16  2016    Unprovoked   
14                                            29-Aug-16  2016    Unprovoked   
15                                            27-Aug-16  2016    Unprovoked   
16                                            25-Aug-16  2016    Unprovoked   
17                                            07-Aug-16  2016    Unprovoked   
18                                            06-Aug-16  2016    Unprovoked   
19                                            04-Aug-16  2016    Unprovoked   
20                                            29-Jul-16  2016    Unprovoked   
21                                            28-Jul-16  2016    Unprovoked   
22                                            28-Jul-16  2016          Boat   
23                                            27-Jul-16  2016      Provoked   
24                                            26-Jul-16  2016    Unprovoked   
25                                            24-Jul-16  2016    Unprovoked   
26                                            23-Jul-16  2016    Unprovoked   
27                                            23-Jul-16  2016    Unprovoked   
28                                            20-Jul-16  2016      Provoked   
29                                            17-Jul-16  2016          Boat   
30                                            16-Jul-16  2016    Unprovoked   
31                                            16-Jul-16  2016    Unprovoked   
32                                            15-Jul-16  2016    Unprovoked   
33                                Reported  14-Jul-2016  2016    Unprovoked   
34                                 Reported 08-Jul-2016  2016    Unprovoked   
35                                            08-Jul-16  2016          Boat   
36                                            07-Jul-16  2016      Provoked   
37                                            07-Jul-16  2016          Boat   
38                                            06-Jul-16  2016    Unprovoked   
39                                            04-Jul-16  2016      Provoked   
40                                            27-Jun-16  2016    Unprovoked   
41                                            25-Jun-16  2016    Unprovoked   
42                                            24-Jun-16  2016    Unprovoked   
43                                            23-Jun-16  2016    Unprovoked   
44                                            21-Jun-16  2016    Unprovoked   
45                                            21-Jun-16  2016    Unprovoked   
46                                            15-Jun-16  2016    Unprovoked   
47                                            15-Jun-16  2016      Provoked   
48                                            14-Jun-16  2016    Unprovoked   
49                                            11-Jun-16  2016    Unprovoked   
50                    

## Checking areas with higher probabilty of attack

In [60]:
areas = data["Area"]
areas = areas.value_counts()
areas.head()

Florida            990
New South Wales    468
None               402
Queensland         300
Hawaii             282
Name: Area, dtype: int64

In [61]:
data["Total Attacks"] = 0
len(data)

5992

In [62]:
# Adding total of Attacks in each row per Area
for num in range(len(data)):
    data.at[num,"Total Attacks"] = areas[data.loc[num,"Area"]]

## Labels and cut offs 

In [64]:
attack_risk = ["Low Risk","Medium Risk","High Risk","Super Risky"]

In [65]:
cutoffs = [10,100,200,500,1000]

In [66]:
bins = pd.cut(data["Total Attacks"],cutoffs, labels=attack_risk)
data["Dangerousness"] = bins


## Reorder and dropping not useful columns

In [23]:
data.columns

Index(['Case Number', 'Date', 'Year', 'Type', 'Country', 'Area', 'Location',
       'Activity', 'Name', 'Sex ', 'Age', 'Injury', 'Fatal (Y/N)', 'Time',
       'Species ', 'Investigator or Source', 'pdf', 'href formula', 'href',
       'Case Number.1', 'Case Number.2', 'original order', 'Total Attacks',
       'Dangerousness'],
      dtype='object')

In [29]:
drops_columns = ["Species ","pdf","href formula","href","Investigator or Source"]

In [30]:
data = data.drop(drops_columns,axis=1)

In [31]:
data.columns

Index(['Case Number', 'Date', 'Year', 'Type', 'Country', 'Area', 'Location',
       'Activity', 'Name', 'Sex ', 'Age', 'Injury', 'Fatal (Y/N)', 'Time',
       'Case Number.1', 'Case Number.2', 'original order', 'Total Attacks',
       'Dangerousness'],
      dtype='object')

In [34]:
reorder = [ 'Date', 'Year', 'Type','Dangerousness', 'Country', 'Area', 'Location',
       'Activity', 'Name', 'Sex ', 'Age', 'Injury', 'Fatal (Y/N)', 'Time','Case Number',
       'Case Number.1', 'Case Number.2', 'Total Attacks','original order']

In [35]:
data = data[reorder]

## Checking genders

In [38]:
data["Sex "].value_counts()

M      4835
F       585
M         2
lli       1
N         1
.         1
Name: Sex , dtype: int64

In [39]:
import folium
attacks_map = folium.Map()

areas = [
    {'loc': [27.994402, -81.760254], 'label': 'Florida'},
    {'loc': [-31.840233, 145.612793], 'label': 'New South Wales'},
    {'loc': [ -20.917574, 142.702789], 'label': 'Queensland'},
    {'loc': [19.896767,-155.582779], 'label': 'Hawaii'},
    {'loc': [36.778259, -119.417931], 'label': 'California'},
    {'loc': [ -28.530554, 30.895824], 'label': 'KwaZulu-Natal'},
    {'loc': [-34.006940, 18.719021], 'label': 'Western Cape Province'},
    {'loc': [-27.672817, 121.628311], 'label': 'Western Australia'},
    {'loc': [ -32.107780, 26.464979], 'label': 'Eastern Cape Province'},
    {'loc': [ 33.836082, -81.163727], 'label': 'South Carolina'}] 

for area in areas:
    marker = folium.Marker(location=area['loc'], popup=area['label'])
    marker.add_to(attacks_map)


In [41]:
data_cleaned = data

In [91]:
data_cleaned.head()

Date  Year        Type Dangerousness    Country      Area  \
0  18-Sep-16  2016  Unprovoked   Super Risky        USA   Florida   
1  18-Sep-16  2016  Unprovoked   Super Risky        USA   Florida   
2  18-Sep-16  2016  Unprovoked   Super Risky        USA   Florida   
3  17-Sep-16  2016  Unprovoked      Low Risk  AUSTRALIA  Victoria   
4  16-Sep-16  2016  Unprovoked      Low Risk  AUSTRALIA  Victoria   

                           Location Activity             Name Sex   Age  \
0  New Smyrna Beach, Volusia County  Surfing             male    M   16   
1  New Smyrna Beach, Volusia County  Surfing   Chucky Luciano    M   36   
2  New Smyrna Beach, Volusia County  Surfing             male    M   43   
3                  Thirteenth Beach  Surfing  Rory Angiolella    M  NaN   
4                       Bells Beach  Surfing             male    M  NaN   

                                  Injury Fatal (Y/N)   Time   Case Number  \
0                  Minor injury to thigh           N  13h00  2016.09.18.c   
1                   Lacerations to hands           N  11h00  2016.09.18.b   
2               Lacerations to lower leg           N  10h43  2016.09.18.a   
3           Struck by fin on chest & leg           N    NaN    2016.09.17   
4  No injury: Knocked off board by shark           N    NaN    2016.09.15   

  Case Number.1 Case Number.2  Total Attacks  original order  
0  2016.09.18.c  2016.09.18.c            990            5993  
1  2016.09.18.b  2016.09.18.b            990            5992  
2  2016.09.18.a  2016.09.18.a            990            5991  
3    2016.09.17    2016.09.17             81            5990  
4    2016.09.16    2016.09.15             81            5989

In [94]:
data_cleaned["Year"].value_counts()

2015    139
2011    128
2014    125
0       124
2013    122
2008    121
2009    120
2012    117
2007    112
2006    103
2016    103
2005    103
2010    101
2000     97
1959     93
1960     93
2001     92
2004     92
2003     92
2002     88
1962     86
1961     78
1995     76
1964     66
1998     65
1999     65
1996     61
1963     61
1966     58
1997     57
1993     56
1994     56
1992     56
1988     55
1958     54
1989     53
1956     51
1965     51
1983     50
1975     49
1981     49
1967     48
1968     46
1950     43
1955     43
1954     42
1970     42
1957     41
1984     41
1942     41
1982     40
1976     39
1986     39
1991     38
1990     38
1974     38
1929     37
1985     37
1953     36
1987     35
1980     35
1972     35
1935     32
1944     31
1949     31
1951     31
1969     30
1937     30
1936     30
1947     30
1948     29
1931     29
1952     29
1971     28
1943     28
1973     27
1932     27
1934     27
1941     27
1946     26
1930     26
1977     26
1928     26
1978

In [11]:
attacks_map

1. Examine data for potential issues.
2. **Identify and fill in missing values.**
3. Identify and correct incorrect values.
4. Remove low variance columns.
5. Identify potential outliers.
6. Correct incorrect data types.
7. Remove special characters and clean categorical variables.
8. **Identify and remove duplicate records.**
9. **Learn how to rename columns in a data frame.**
10. **Change the order of a data frame's columns.**
11. **Filter records based on conditional statements.**
12. **Create additional categories via binning and conditional statements.**
13. Learn how to one-hot encode categorical variables.
14. Combine data frames via merging and concatenation.
15. Melt data from wide format into long format.

In [2]:
    '''
list_country = list(country[country > 100].index)
list_country
data[data['Country'].isin(list_country)]
years = data["Year"] > 1999
data[data['Year']>1999]
    '''

'\nlist_country = list(country[country > 100].index)\nlist_country\ndata[data[\'Country\'].isin(list_country)]\nyears = data["Year"] > 1999\ndata[data[\'Year\']>1999]\n'

In [101]:
years = data_cleaned["Year"] > 1595.index

SyntaxError: invalid syntax (<ipython-input-101-34a1c0fd01a1>, line 1)